In [1]:
# IGNORE THIS FILE
import numpy as np
import pandas as pd

import plotly.express as px #for visualization
import matplotlib.pyplot as plt #for visualization


from sklearn.preprocessing import LabelEncoder
!ls
data_df = pd.read_excel("../Dataset/customer_churn_large_dataset.xlsx")


# data_df['Total_Usage_GB_Per_Month'] = data_df['Total_Usage_GB'] / data_df['Subscription_Length_Months']

gender_mapping = {'Male': 1, 'Female': 0}
location_mapping = {'Los Angeles': 0, 'Chicago': 1, 'Miami': 2, 'New York': 3, 'Houston': 4}

# data_df['Gender'] = gender_mapping(data_df['Gender'])
# data_df['Location'] = location_mapping(data_df['Location'])

# Apply gender mapping to the 'Gender' column
data_df['Gender'] = data_df['Gender'].map(gender_mapping)

# Apply location mapping to the 'Location' column
data_df['Location'] = data_df['Location'].map(location_mapping)

print(data_df.head())


t1.ipynb
   CustomerID        Name  Age  Gender  Location  Subscription_Length_Months  \
0           1  Customer_1   63       1         0                          17   
1           2  Customer_2   62       0         3                           1   
2           3  Customer_3   24       0         0                           5   
3           4  Customer_4   36       0         2                           3   
4           5  Customer_5   46       0         2                          19   

   Monthly_Bill  Total_Usage_GB  Churn  
0         73.36             236      0  
1         48.76             172      0  
2         85.47             460      0  
3         97.94             297      1  
4         58.14             266      0  


# New section

In [3]:
target_instance = data_df["Churn"].value_counts().to_frame()
target_instance = target_instance.reset_index()
target_instance = target_instance.rename(columns={'index': 'Category'})
fig = px.pie(target_instance, values='Churn', names='Category', color_discrete_sequence=["green", "red"],
             title='Distribution of Churn')
fig.show()

In [4]:
#Defining bar chart function
def bar(feature, df=data_df ):
    #Groupby the categorical feature
    temp_df = df.groupby([feature, 'Churn']).size().reset_index()
    temp_df = temp_df.rename(columns={0:'Count'})
    #Calculate the value counts of each distribution and it's corresponding Percentages
    value_counts_df = df[feature].value_counts().to_frame().reset_index()
    categories = [cat[1][0] for cat in value_counts_df.iterrows()]
    #Calculate the value counts of each distribution and it's corresponding Percentages
    num_list = [num[1][1] for num in value_counts_df.iterrows()]
    div_list = [element / sum(num_list) for element in num_list]
    percentage = [round(element * 100,1) for element in div_list]
    #Defining string formatting for graph annotation
    #Numeric section
    def num_format(list_instance):
        formatted_str = ''
        for index,num in enumerate(list_instance):
            if index < len(list_instance)-2:
                formatted_str=formatted_str+f'{num}%, ' #append to empty string(formatted_str)
            elif index == len(list_instance)-2:
                formatted_str=formatted_str+f'{num}% & '
            else:
                formatted_str=formatted_str+f'{num}%'
        return formatted_str
    #Categorical section
    def str_format(list_instance):
        formatted_str = ''
        for index, cat in enumerate(list_instance):
            if index < len(list_instance)-2:
                formatted_str=formatted_str+f'{cat}, '
            elif index == len(list_instance)-2:
                formatted_str=formatted_str+f'{cat} & '
            else:
                formatted_str=formatted_str+f'{cat}'
        return formatted_str
    #Running the formatting functions
    num_str = num_format(percentage)
    cat_str = str_format(categories)

    #Setting graph framework
    fig = px.bar(temp_df, x=feature, y='Count', color='Churn', title=f'Churn rate by {feature}', barmode="group", color_discrete_sequence=["green", "red"])
    fig.add_annotation(
                text=f'Value count of distribution of {cat_str} are<br>{num_str} percentage respectively.',
                align='left',
                showarrow=False,
                xref='paper',
                yref='paper',
                x=1.4,
                y=1.3,
                bordercolor='black',
                borderwidth=1)
    fig.update_layout(
        # margin space for the annotations on the right
        margin=dict(r=400),
    )

    return fig.show()

In [5]:
bar('Gender')
#Partner feature plot
bar('Age')
#Dependents feature plot
bar('Location')
bar('Subscription_Length_Months')
bar('Monthly_Bill')
bar('Total_Usage_GB')


In [97]:
bar('Monthly_Bill')

In [6]:
def hist(feature):
    group_df = data_df.groupby([feature, 'Churn']).size().reset_index()
    group_df = group_df.rename(columns={0: 'Count'})
    fig = px.histogram(group_df, x=feature, y='Count', color='Churn', marginal='box', title=f'Churn rate frequency to {feature} distribution', color_discrete_sequence=["green", "red"])
    fig.show()


hist("Subscription_Length_Months")
hist("Monthly_Bill")
hist("Total_Usage_GB_Per_Month")


In [2]:
data_df.drop(["CustomerID","Name"],axis=1,inplace = True)


# Encode categorical features

#Defining the map function
# def binary_map(feature):
#     return feature.map({'Yes':1, 'No':0})

## Encoding target feature

##data_df['Churn'] = data_df[['Churn']].apply(binary_map)

# Encoding gender category
# data_df['Gender'] = data_df['Gender'].map({'Male':1, 'Female':0})

# data_df['Location'] = data_df['Location'].map({'Los Angeles' : 0 , 'New York': 1 , 'Miami' : 2 , 'Chicago' : 3 , 'Houston' : 4})



#Encoding the other categoric features with more than two categories
#data_df =  pd.get_dummies(data_df, columns=['Gender', 'Location'])



# Calculate Monthly Bill to Subscription Length Ratio
# data_df['Bill_Subscription_Ratio'] = data_df['Monthly_Bill'] / data_df['Subscription_Length_Months']

# # Calculate Monthly Usage Deviation
# average_monthly_usage = data_df['Total_Usage_GB'].mean()
# data_df['Monthly_Usage_Deviation'] = data_df['Total_Usage_GB'] - average_monthly_usage

# # Calculate Monthly Bill Deviation
# average_monthly_bill = data_df['Monthly_Bill'].mean()
# data_df['Monthly_Bill_Deviation'] = data_df['Monthly_Bill'] - average_monthly_bill

# # Calculate the ratio of Monthly Bill to Total Usage GB
# data_df['Bill_to_Usage_Ratio'] = data_df['Monthly_Bill'] / data_df['Total_Usage_GB']

# # Calculate the difference between Subscription Length and Age (assuming age is in months)
# data_df['Subscription_Length_Age_Diff'] = data_df['Subscription_Length_Months'] - data_df['Age']

# # Create a binary feature to indicate if the monthly usage is significantly above average
# average_monthly_usage = data_df['Total_Usage_GB'].mean()
# data_df['High_Usage'] = (data_df['Total_Usage_GB'] > average_monthly_usage).astype(int)


In [8]:
corr = data_df.corr()

fig = px.imshow(corr,width=1000, height=1000)
fig.show()

/tmp/ipykernel_60585/4144796732.py:1: FutureWarning:

The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.



In [3]:
#feature scaling
from sklearn.preprocessing import MinMaxScaler
sc = MinMaxScaler()
# data_df['Age'] = sc.fit_transform(data_df[['Age']])
# data_df['Location'] = sc.fit_transform(data_df[['Location']])
data_df['Subscription_Length_Months'] = sc.fit_transform(data_df[['Subscription_Length_Months']])
data_df['Monthly_Bill'] = sc.fit_transform(data_df[['Monthly_Bill']])
data_df['Total_Usage_GB'] = sc.fit_transform(data_df[['Total_Usage_GB']])
# data_df['Total_Usage_GB_Per_Month'] = sc.fit_transform(data_df[['Total_Usage_GB_Per_Month']])
# data_df['Bill_Subscription_Ratio'] = sc.fit_transform(data_df[['Bill_Subscription_Ratio']])
# data_df['Monthly_Usage_Deviation'] = sc.fit_transform(data_df[['Monthly_Usage_Deviation']])
# data_df['Monthly_Bill_Deviation'] = sc.fit_transform(data_df[['Monthly_Bill_Deviation']])
# data_df['Bill_to_Usage_Ratio'] = sc.fit_transform(data_df[['Bill_to_Usage_Ratio']])
# data_df['Subscription_Length_Age_Diff'] = sc.fit_transform(data_df[['Subscription_Length_Age_Diff']])
# data_df['High_Usage'] = sc.fit_transform(data_df[['High_Usage']])

In [4]:
print(data_df.head())


   Age  Gender  Location  Subscription_Length_Months  Monthly_Bill  \
0   63       1         0                    0.695652      0.619429   
1   62       0         3                    0.000000      0.268000   
2   24       0         0                    0.173913      0.792429   
3   36       0         2                    0.086957      0.970571   
4   46       0         2                    0.782609      0.402000   

   Total_Usage_GB  Churn  
0        0.413333      0  
1        0.271111      0  
2        0.911111      0  
3        0.548889      1  
4        0.480000      0  


In [5]:
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB

#Import metric for performance evaluation
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

from sklearn.model_selection import GridSearchCV



#Split data into train and test sets
from sklearn.model_selection import train_test_split
X = data_df.drop('Churn', axis=1)
y = data_df['Churn']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=250)

#Defining the modelling function
def modeling(alg, alg_name, params={}):
    model = alg(**params) #Instantiating the algorithm class and unpacking parameters if any
    model.fit(X_train, y_train)

    y_pred = model.predict(X_test)

    #Performance evaluation
    def print_scores(alg, y_true, y_pred):
        print(alg_name)
        acc_score = accuracy_score(y_true, y_pred)
        print("accuracy: ",acc_score)
        pre_score = precision_score(y_true, y_pred)
        print("precision: ",pre_score)
        rec_score = recall_score(y_true, y_pred)
        print("recall: ",rec_score)
        f_score = f1_score(y_true, y_pred, average='weighted')
        print("f1_score: ",f_score)

    print_scores(alg, y_test, y_pred)
    return model

# Running logistic regression model
log_model = modeling(LogisticRegression, 'Logistic Regression')


Logistic Regression
accuracy:  0.5015666666666667
precision:  0.5105593607305936
recall:  0.11905237239635323
f1_score:  0.41584792749586946


In [6]:
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LogisticRegression

# Define a grid of hyperparameters to search
param_grid = {
    'C': [0.001, 0.01, 0.1, 1, 10, 100],
    'penalty': ['l2']
}

# Create a logistic regression model
model = LogisticRegression()

# Use GridSearchCV to find the best hyperparameters
grid_search = GridSearchCV(model, param_grid, cv=5, scoring='accuracy')
grid_search.fit(X, y)

# Get the best hyperparameters
best_params = grid_search.best_params_
print("Best Hyperparameters:", best_params)






from sklearn.linear_model import LogisticRegression

# Instantiate a logistic regression model with the best hyperparameters
best_model = LogisticRegression(C=best_params['C'], penalty=best_params['penalty'])

# Train the model on your full training dataset
best_model.fit(X_train, y_train)


from sklearn.metrics import accuracy_score, classification_report

# Make predictions on the test dataset
y_pred = best_model.predict(X_test)

# Calculate accuracy and other relevant metrics
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print("Model Accuracy:", accuracy)
print("Classification Report:\n", report)



Best Hyperparameters: {'C': 10, 'penalty': 'l2'}
Model Accuracy: 0.5015666666666667
Classification Report:
               precision    recall  f1-score   support

           0       0.50      0.89      0.64     14973
           1       0.51      0.12      0.19     15027

    accuracy                           0.50     30000
   macro avg       0.51      0.50      0.42     30000
weighted avg       0.51      0.50      0.42     30000



In [7]:
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LogisticRegression

model = LogisticRegression()

# Perform 5-fold cross-validation
scores = cross_val_score(model, X, y, cv=5, scoring='accuracy')
print("Cross-Validation Accuracy:", scores.mean())

Cross-Validation Accuracy: 0.5007900000000001


In [82]:
from sklearn.feature_selection import RFECV
from sklearn.model_selection import StratifiedKFold
log = LogisticRegression()
rfecv = RFECV(estimator=log, cv=StratifiedKFold(10, random_state=50, shuffle=True), scoring="accuracy")
rfecv.fit(X, y)

RFECV(cv=StratifiedKFold(n_splits=10, random_state=50, shuffle=True),
      estimator=LogisticRegression(), scoring='accuracy')

In [8]:
### Trying other machine learning algorithms: SVC
svc_model = modeling(SVC, 'SVC Classification')

In [83]:
#Random forest
rf_model = modeling(RandomForestClassifier, "Random Forest Classification")

Random Forest Classification
accuracy:  0.49693333333333334
precision:  0.4942219071251329
recall:  0.46694353272154865
f1_score:  0.49648794596278095


In [85]:
#Decision tree
dt_model = modeling(DecisionTreeClassifier, "Decision Tree Classification")

Decision Tree Classification
accuracy:  0.5023
precision:  0.4999330835117773
recall:  0.5004353941992096
f1_score:  0.5023010534838797


In [84]:
#Naive bayes
nb_model = modeling(GaussianNB, "Naive Bayes Classification")

Naive Bayes Classification
accuracy:  0.4992333333333333
precision:  0.4951436247158504
recall:  0.32098600040190234
f1_score:  0.4829504314568535


In [9]:
!pip install --upgrade tensorflow


import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from tensorflow import keras
from tensorflow.keras import layers

scaler = MinMaxScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

# Build a Deep Neural Network (DNN)
model = keras.Sequential()
model.add(layers.Input(shape=(X_train_scaled.shape[1],)))
model.add(layers.Dense(64, activation='relu'))
model.add(layers.Dense(32, activation='relu'))
model.add(layers.Dense(1, activation='sigmoid'))

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(X_train_scaled, y_train, epochs=10, batch_size=32, validation_split=0.2)

# Evaluate the model
y_pred = (model.predict(X_test_scaled) > 0.5).astype(int)
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1-Score:", f1)

Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for tensorflow from https://files.pythonhosted.org/packages/c2/20/b15abac0be474f12cf51a104c9dd935b053081b502c103e9e947e8be7b84/tensorflow-2.13.1-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata
  Obtaining dependency information for flatbuffers>=23.1.21 from https://files.pythonhosted.org/packages/6f/12/d5c79ee252793ffe845d58a913197bfa02ae9a0b5c9bc3dc4b58d477b9e7/flatbuffers-23.5.26-py2.py3-none-any.whl.metadata
  Obtaining dependency information for keras<2.14,>=2.13.1 from https://files.pythonhosted.org/packages/2e/f3/19da7511b45e80216cbbd9467137b2d28919c58ba1ccb971435cb631e470/keras-2.13.1-py3-none-any.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 3.4 MB/s eta 0:00:0000:0100:010m
  Obtaining dependency information for tensorflow-estimator<2.14,>=2.13.0 from https://files.pythonhosted.org/packages/72/5c/c318268d96791c6222ad7df1651bb

TypeError: Descriptors cannot not be created directly.
If this call came from a _pb2.py file, your generated code is out of date and must be regenerated with protoc >= 3.19.0.
If you cannot immediately regenerate your protos, some other possible workarounds are:
 1. Downgrade the protobuf package to 3.20.x or lower.
 2. Set PROTOCOL_BUFFERS_PYTHON_IMPLEMENTATION=python (but this will use pure-Python parsing and will be much slower).

More information: https://developers.google.com/protocol-buffers/docs/news/2022-05-06#python-updates

In [76]:
#Saving best model
import joblib
#Sava the model to disk
filename = 'model.sav'
print(log_model)
joblib.dump(log_model, filename)
!ls

LogisticRegression()
customer_churn_large_dataset.xlsx  t1.ipynb	    Untitled.ipynb
model.sav			   Untitled1.ipynb
streamlit1.py			   Untitled2.ipynb
